In [1]:
product_reccomended_url = 'https://www.central.co.th/th/beauty/fragrance?page=1'
product_new_arrival_url = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_created_at_desc'
product_cheap_to_expensive = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_final_price_asc'
product_expensive_to_cheap = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_final_price_desc'
product_discount_low_to_high = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_discount_percentage_asc'
product_discount_high_to_low = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_discount_percentage_desc'
product_desc_commented = 'https://www.central.co.th/th/beauty/fragrance?sortBy=cds_th_products_rating_count_desc'

In [2]:
import requests
# url = product_reccomended_url
# response = requests.get(url)
# print(response)

In [3]:
import sys
sys.path.insert(0,'Recommendation_System\chromedriver.exe')

import jsonify
import time
import pandas as pd
from bs4 import BeautifulSoup
from selenium import webdriver
import chromedriver_autoinstaller
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait  # Wait for elements to load
from selenium.webdriver.support import expected_conditions as EC  # Conditions to wait for (like visibility of elements)

# setup chrome options
chrome_options = webdriver.ChromeOptions()
chrome_options.add_argument('--headless') # ensure GUI is off
chrome_options.add_argument('--no-sandbox')
chrome_options.add_argument('--disable-dev-shm-usage')

# set path to chromedriver as per your configuration
chromedriver_autoinstaller.install()

# # set up the webdriver
# driver = webdriver.Chrome(options=chrome_options)
# driver.get(url)



'c:\\Users\\ASUS\\anaconda3\\envs\\Transformers\\lib\\site-packages\\chromedriver_autoinstaller\\129\\chromedriver.exe'

In [4]:
from selenium.webdriver.support.ui import WebDriverWait  # Wait for elements to load
from selenium.webdriver.support import expected_conditions as EC  # Conditions to wait for (like visibility of elements)



In [5]:
results = []

In [18]:
def fetch_and_parse(url, max_retries=3, delay=1):
    for attempt in range(max_retries):
        try:
            response = requests.get(url)
            response.raise_for_status()  # Raises an HTTPError for bad responses
            return BeautifulSoup(response.content, 'html.parser')
        except requests.RequestException as e:
            print(f"Attempt {attempt + 1} failed: {e}")
            if attempt < max_retries - 1:
                time.sleep(delay)
    return None

def extract_image_src(url):
    soup = fetch_and_parse(url)
    if not soup:
        return None

    # Try different selectors
    selectors = [
        {'data-testid': 'img-viewProductImage-mainSlider0'},
        {'class': 'product-image'},  # Example: adjust based on actual HTML
        {'id': 'main-product-image'}  # Example: adjust based on actual HTML
    ]

    for selector in selectors:
        img = soup.find('img', attrs=selector)
        if img and 'src' in img.attrs:
            return img['src']

    # If no image found, print the page source for debugging
    print("Image not found. Page source:")
    print(soup.prettify())
    return None

In [21]:
import re
index = 12
while index <= 24:
    results = []
    url = 'https://www.central.co.th/th/beauty/fragrance?page=' + f'{index}'
    # while index <= 24 :
    driver = webdriver.Chrome(options=chrome_options)
    driver.get(url)
    time.sleep(5)
    html = driver.page_source
    mysoup = BeautifulSoup(html, "html.parser")
    job_elements = mysoup.find_all("div" , class_ = "flip-card-front")
    for job_element in job_elements:
        product = job_element.find("a" , class_ = 'sliderTitle').text
        detail_1 = job_element.find("a" , class_ = 'sliderDesc').text
        final_price = job_element.find("h4" , class_ = 'finalPrice').text
        if job_element.find('div' , class_ = "originPrice") is not None:
            origin_price = job_element.find('div' , class_ = "originPrice").text
            discount = job_element.find('div' , class_ = 'savePrice').text
            discount = discount + ' ' +job_element.find('span' , class_ = 'flip-card-front__perDiscount').text
        else :
            origin_price = final_price
            discount = 0
        # img = job_element.find("img")['src']
        link = 'https://www.central.co.th/'+ job_element.find("a")['href']
        # print(img)
        # print(link)

        if job_element.find("span" , class_ = 'red-stars'):
            rating = job_element.find("span" , class_ = 'red-stars')
            commentation = job_element.find("label").text
            rating = rating['style']
            rating = re.search('\d\.*\d*' , rating)
            rating = rating.group()
            rating = f"rating (เต็ม 5 คะแนน): {rating.strip()}"
        else : 
            rating = 'no rating yet'
            commentation = 0
        

        response = requests.get(link)
        detail_soup = BeautifulSoup(response.content , 'html.parser')
        # img = detail_soup.find('img', attrs={'data-testid': 'img-viewProductImage-mainSlider0'})['src']
        img = extract_image_src(link)
        product_detail = detail_soup.find('div' , class_ = 'accordion-body')
        if product_detail is not None:
            product_detail_3 = product_detail.find_all('li')
            product_detail_2 = product_detail.find_all('p')
        else :
            product_detail_2 = ''
            product_detail_3 = ''


        detail_2 = ''
        for sentence in product_detail_2:
            
            text = sentence.text.strip()  # ตัดช่องว่าง
            if 'หมายเหตุ' in text or 'caution' in text.lower() or text == '':
                continue
            else:
                detail_2 += text

        detail_3 = ''
        for sentence in product_detail_3:
            detail_3 += sentence.text.strip()+'\n'

        if commentation != 0:
            driver.get(link)
            time.sleep(2)
            detail = driver.find_element(By.CLASS_NAME , 'review-content')
            more_detail = detail.find_elements(By.CLASS_NAME, 'review-details')
            comments = []
            for p in more_detail:
                comment = ''
                inner_html = p.get_attribute('innerHTML')
                # print(inner_html)
                soupp = BeautifulSoup(inner_html , 'html.parser')
                # review = soupp.find(class_='reviewTitle').get_text(strip = True)
                # review_detail = soupp.find(class_ = 'full-text').get_text(strip = True)
                review = soupp.find(class_='reviewTitle')
                if review is not None:
                    review_text = review.get_text(strip=True)
                else:
                    review_text = ''

                # Extract the review detail (if exists)
                review_detail_element = soupp.find(class_='full-text')
                if review_detail_element is not None:
                    if review_detail_element.get_text(strip=True) == 'no_detail':
                        review_detail = ''
                    else:
                        review_detail = review_detail_element.get_text(strip=True)
                else:
                    review_detail = ''

                # Print or append results

                print(review.text , review_detail)

                comments.append({'head_comment': review.text , 'detail_comment' : review_detail})
                
        else :
            comments = []


        results.append({
                'Product': product.strip(),
                'Origin_Price' : origin_price.strip(),
                'Discount' : discount,  
                'Price': final_price.strip() ,
                'rating' : rating.strip() , 
                'detail' : detail_1.strip() ,
                'detail_2' : detail_2 ,
                'detail_3' : detail_3 ,
                'detail_link' : link ,
                'total_comments' : commentation ,
                'top_comments' : comments ,
                'Image' : img
            })
        
        driver.back()
        # index += 1
        # url = 'https://www.central.co.th/th/beauty/fragrance?page=' + f'{index}'

    import json
    filename = f'results{index}.json'

    # Save to JSON file
    with open(filename, 'w', encoding='utf-8') as json_file:
        json.dump(results, json_file, ensure_ascii=False, indent=4)

    print(f"Data saved to {filename}")
    index += 1
        



Image not found. Page source:
<!DOCTYPE HTML>
<html lang="th">
 <head>
  <meta charset="utf-8"/>
  <title>
   KIRINATU น้ำหอม Parfum 100 ml.  La Vie En Rose | ของแท้ 100% | Central Online
  </title>
  <meta content="น้ำหอม Parfum 100 ml.  La Vie En Rose จากKIRINATU มีวางจำหน่ายแล้วที่ Central Online ไปเลือกช้อปกันได้เลย รับประกันคุณภาพ ของแท้แน่นอน" name="description"/>
  <meta content="product-page" name="template"/>
  <meta content="width=device-width, initial-scale=1.0, maximum-scale=3.0" name="viewport"/>
  <meta content="index,follow" name="robots"/>
  <!-- Default  -->
  <script type="module">
   window.RUM_BASE = window.origin;
  import { sampleRUM } from '/.rum/@adobe/helix-rum-js@%5E2/src/index.js';
  window.hlx = window.hlx || {};
  window.hlx.sampleRUM = sampleRUM;
  sampleRUM();
  </script>
  <link href="/content/dam/cds/favicon.ico" rel="icon" type="image/x-icon"/>
  <!-- Modern Browser  -->
  <link href="/content/dam/cds/favicon.svg" rel="icon" type="image/svg+xml"/>
  <l

In [20]:
results = []
url = 'https://www.central.co.th/th/beauty/fragrance?page=7'
# while index <= 24 :
driver = webdriver.Chrome(options=chrome_options)
driver.get(url)
time.sleep(5)
html = driver.page_source
mysoup = BeautifulSoup(html, "html.parser")
job_elements = mysoup.find_all("div" , class_ = "flip-card-front")
for job_element in job_elements:
    product = job_element.find("a" , class_ = 'sliderTitle').text
    detail_1 = job_element.find("a" , class_ = 'sliderDesc').text
    final_price = job_element.find("h4" , class_ = 'finalPrice').text
    if job_element.find('div' , class_ = "originPrice") is not None:
        origin_price = job_element.find('div' , class_ = "originPrice").text
        discount = job_element.find('div' , class_ = 'savePrice').text
        discount = discount + ' ' +job_element.find('span' , class_ = 'flip-card-front__perDiscount').text
    else :
        origin_price = final_price
        discount = 0
    # img = job_element.find("img")['src']
    link = 'https://www.central.co.th/'+ job_element.find("a")['href']
    # print(img)
    # print(link)

    if job_element.find("span" , class_ = 'red-stars'):
        rating = job_element.find("span" , class_ = 'red-stars')
        commentation = job_element.find("label").text
        rating = rating['style']
        rating = re.search('\d\.*\d*' , rating)
        rating = rating.group()
        rating = f"rating (เต็ม 5 คะแนน): {rating.strip()}"
    else : 
        rating = 'no rating yet'
        commentation = 0
    

    response = requests.get(link)
    detail_soup = BeautifulSoup(response.content , 'html.parser')
    # img = detail_soup.find('img', attrs={'data-testid': 'img-viewProductImage-mainSlider0'})['src']
    img = extract_image_src(link)
    product_detail = detail_soup.find('div' , class_ = 'accordion-body')
    if product_detail is not None:
        product_detail_3 = product_detail.find_all('li')
        product_detail_2 = product_detail.find_all('p')
    else :
        product_detail_2 = ''
        product_detail_3 = ''


    detail_2 = ''
    for sentence in product_detail_2:
        
        text = sentence.text.strip()  # ตัดช่องว่าง
        if 'หมายเหตุ' in text or 'caution' in text.lower() or text == '':
            continue
        else:
            detail_2 += text

    detail_3 = ''
    for sentence in product_detail_3:
        detail_3 += sentence.text.strip()+'\n'

    if commentation != 0:
        driver.get(link)
        time.sleep(2)
        detail = driver.find_element(By.CLASS_NAME , 'review-content')
        more_detail = detail.find_elements(By.CLASS_NAME, 'review-details')
        comments = []
        for p in more_detail:
            comment = ''
            inner_html = p.get_attribute('innerHTML')
            # print(inner_html)
            soupp = BeautifulSoup(inner_html , 'html.parser')
            # review = soupp.find(class_='reviewTitle').get_text(strip = True)
            # review_detail = soupp.find(class_ = 'full-text').get_text(strip = True)
            review = soupp.find(class_='reviewTitle')
            if review is not None:
                review_text = review.get_text(strip=True)
            else:
                review_text = ''

            # Extract the review detail (if exists)
            review_detail_element = soupp.find(class_='full-text')
            if review_detail_element is not None:
                if review_detail_element.get_text(strip=True) == 'no_detail':
                    review_detail = ''
                else:
                    review_detail = review_detail_element.get_text(strip=True)
            else:
                review_detail = ''

            # Print or append results

            print(review.text , review_detail)

            comments.append({'head_comment': review.text , 'detail_comment' : review_detail})
            
    else :
        comments = []


    results.append({
            'Product': product.strip(),
            'Origin_Price' : origin_price.strip(),
            'Discount' : discount,  
            'Price': final_price.strip() ,
            'rating' : rating.strip() , 
            'detail' : detail_1.strip() ,
            'detail_2' : detail_2 ,
            'detail_3' : detail_3 ,
            'detail_link' : link ,
            'total_comments' : commentation ,
            'top_comments' : comments ,
            'Image' : img
        })
    
    driver.back()
    # index += 1
    # url = 'https://www.central.co.th/th/beauty/fragrance?page=' + f'{index}'

import json
filename = f'results{index}.json'

# Save to JSON file
with open(filename, 'w', encoding='utf-8') as json_file:
    json.dump(results, json_file, ensure_ascii=False, indent=4)

print(f"Data saved to {filename}")

Attempt 1 failed: 404 Client Error: Not Found for url: https://www.central.co.th//th/davidoff-men-fragrance-cool-water-reborn-men-edp-grcds11523090038
Attempt 2 failed: 404 Client Error: Not Found for url: https://www.central.co.th//th/davidoff-men-fragrance-cool-water-reborn-men-edp-grcds11523090038
Attempt 3 failed: 404 Client Error: Not Found for url: https://www.central.co.th//th/davidoff-men-fragrance-cool-water-reborn-men-edp-grcds11523090038
Data saved to results12.json


In [ ]:
url = 'https://www.central.co.th/th/harnn-juniper-berry-cedarwood-eau-de-toilette-45-ml-mkp1584275'
response = requests.get(link)
detail_soup = BeautifulSoup(response.content , 'html.parser')
img = detail_soup.find('img', attrs={'data-testid': 'img-viewProductImage-mainSlider0'})['src']

In [12]:
print(img)

None


In [17]:
import requests
from bs4 import BeautifulSoup
import time

def fetch_and_parse(url, max_retries=3, delay=1):
    for attempt in range(max_retries):
        try:
            response = requests.get(url)
            response.raise_for_status()  # Raises an HTTPError for bad responses
            return BeautifulSoup(response.content, 'html.parser')
        except requests.RequestException as e:
            print(f"Attempt {attempt + 1} failed: {e}")
            if attempt < max_retries - 1:
                time.sleep(delay)
    return None

def extract_image_src(url):
    soup = fetch_and_parse(url)
    if not soup:
        return None

    # Try different selectors
    selectors = [
        {'data-testid': 'img-viewProductImage-mainSlider0'},
        {'class': 'product-image'},  # Example: adjust based on actual HTML
        {'id': 'main-product-image'}  # Example: adjust based on actual HTML
    ]

    for selector in selectors:
        img = soup.find('img', attrs=selector)
        if img and 'src' in img.attrs:
            return img['src']

    # If no image found, print the page source for debugging
    print("Image not found. Page source:")
    print(soup.prettify())
    return None


